Michael Ersevim DSC550 - Week 3

In [4]:
import pandas as pd
import sys
import unicodedata
#import nltk
#nltk.download('stopwords')
#nltk.download('punkt')
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.stem.porter import PorterStemmer
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
#from sklearn.feature_extraction.text import TdfifVectorizer
from textblob import TextBlob
from sklearn.metrics import accuracy_score


In [1]:
#pip install scikit-learn==0.13 # Note - this wasn't working and one of the suggestions online was to upgrade
    # to version 0.13. It unfortunately did NOT fix some subsequent issues further down in part 2...

  Using cached scikit-learn-0.13.tar.gz (3.5 MB)
  Running setup.py clean for scikit-learn
Failed to build scikit-learn
  Attempting uninstall: scikit-learn
    Found existing installation: scikit-learn 0.24.0
    Uninstalling scikit-learn-0.24.0:
      Successfully uninstalled scikit-learn-0.24.0
    Running setup.py install for scikit-learn: started
    Running setup.py install for scikit-learn: finished with status 'error'
  Rolling back uninstall of scikit-learn
  Moving to c:\users\mersevim\appdata\local\continuum\miniconda3\envs\tensorflow-gpu\lib\site-packages\scikit_learn-0.24.0.dist-info\
   from c:\users\mersevim\appdata\local\continuum\miniconda3\envs\tensorflow-gpu\lib\site-packages\~cikit_learn-0.24.0.dist-info
  Moving to c:\users\mersevim\appdata\local\continuum\miniconda3\envs\tensorflow-gpu\lib\site-packages\sklearn\
   from c:\users\mersevim\appdata\local\continuum\miniconda3\envs\tensorflow-gpu\lib\site-packages\~klearn
Note: you may need to restart the kernel to use

  ERROR: Command errored out with exit status 1:
   command: 'C:\Users\mersevim\AppData\Local\Continuum\miniconda3\envs\tensorflow-gpu\python.exe' -u -c 'import sys, setuptools, tokenize; sys.argv[0] = '"'"'C:\\Users\\mersevim\\AppData\\Local\\Temp\\pip-install-5qxcn8__\\scikit-learn_cc1de2f55cba424cb5186bc168514142\\setup.py'"'"'; __file__='"'"'C:\\Users\\mersevim\\AppData\\Local\\Temp\\pip-install-5qxcn8__\\scikit-learn_cc1de2f55cba424cb5186bc168514142\\setup.py'"'"';f=getattr(tokenize, '"'"'open'"'"', open)(__file__);code=f.read().replace('"'"'\r\n'"'"', '"'"'\n'"'"');f.close();exec(compile(code, __file__, '"'"'exec'"'"'))' bdist_wheel -d 'C:\Users\mersevim\AppData\Local\Temp\pip-wheel-kyf4512j'
       cwd: C:\Users\mersevim\AppData\Local\Temp\pip-install-5qxcn8__\scikit-learn_cc1de2f55cba424cb5186bc168514142\
  Complete output (983 lines):
  Partial import of sklearn during the build process.
  Copying source tree into build/py3k for 2to3 transformation...
  Converting to Python3 v

  copying sklearn\linear_model\coordinate_descent.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\least_angle.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\logistic.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\omp.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\passive_aggressive.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\perceptron.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\randomized_l1.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\ridge.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\setup.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\stochastic_gradient.py -> build\lib.win-amd64-3.7\sklearn\linear_model
  copying sklearn\linear_model\__init__.py -> build\lib.win-

In [ ]:
#pip install -U textblob # This was required before importing

In [6]:
df = pd.read_csv (r'labeledTrainData.tsv', sep = '\t')   # needed to add the seperator since the values were tab delimited
df.head(10) # defaults to 5 rows, unless specified in '()'
# Import csv and show top 10 rows

id  sentiment                                             review
0   5814_8          1  With all this stuff going down at the moment w...
1   2381_9          1  \The Classic War of the Worlds\" by Timothy Hi...
2   7759_3          0  The film starts with a manager (Nicholas Bell)...
3   3630_4          0  It must be assumed that those who praised this...
4   9495_8          1  Superbly trashy and wondrously unpretentious 8...
5   8196_8          1  I dont know why people think this is such a ba...
6   7166_2          0  This movie could have been very good, but come...
7  10633_1          0  I watched this video at a friend's house. I'm ...
8    319_1          0  A friend of mine bought this film for £1, and ...
9  8713_10          1  <br /><br />This movie is full of references. ...

In [7]:
df.shape # let's us check for all cols and 25,000 rows

(25000, 3)

In [8]:
def makepolarity(text): # Defining a function to return a raw decimal polarity on the review
    return TextBlob(text).sentiment.polarity

In [9]:
df['polarity'] = df['review'].apply(makepolarity) # iterates through the reviews and scores - calls in the function above

In [10]:
df['blob_sentiment'] = (df['polarity'] >= 0).astype(int) # forces negatives to be '0'; all else 1

In [11]:
df.head(15) # check if looks ok

id  sentiment                                             review  \
0    5814_8          1  With all this stuff going down at the moment w...   
1    2381_9          1  \The Classic War of the Worlds\" by Timothy Hi...   
2    7759_3          0  The film starts with a manager (Nicholas Bell)...   
3    3630_4          0  It must be assumed that those who praised this...   
4    9495_8          1  Superbly trashy and wondrously unpretentious 8...   
5    8196_8          1  I dont know why people think this is such a ba...   
6    7166_2          0  This movie could have been very good, but come...   
7   10633_1          0  I watched this video at a friend's house. I'm ...   
8     319_1          0  A friend of mine bought this film for £1, and ...   
9   8713_10          1  <br /><br />This movie is full of references. ...   
10   2486_3          0  What happens when an army of wetbacks, towelhe...   
11  6811_10          1  Although I generally do not like remakes belie...   
12  11744_9          1  \Mr. Harvey Lights a Candle\" is anchored by a...   
13   7369_1          0  I had a feeling that after \Submerged\", this ...   
14  12081_1          0  note to George Litman, and others: the Mystery...   

    polarity  blob_sentiment  
0   0.001277               1  
1   0.256349               1  
2  -0.053941               0  
3   0.134753               1  
4  -0.024842               0  
5   0.105882               1  
6  -0.027054               0  
7   0.068750               1  
8   0.098810               1  
9   0.258333               1  
10 -0.030556               0  
11  0.238244               1  
12  0.054477               1  
13  0.070696               1  
14  0.142071               1

In [12]:
score = accuracy_score(df['sentiment'], df['blob_sentiment']) # using a library to score the accuracy.
score

0.68524

Looks like the overall TextBlob accuracy score is a little better than 2 out of 3.

In [ ]:
# The extra credit attempt did not work out well - I tried setting up the same 
# structure as above, but the library was mising something

In [ ]:
vader_analyzer = SentimentIntensityAnalyzer() # Three of these next four blocks will return errors

In [14]:
def vaderpolarity(text):
    return vader_analyzer(text).polarity_scores

In [ ]:
df['vader_polarity'] = df['review'].apply(vaderpolarity)

In [ ]:
df['vader_sentiment'] = (df['vader_polarity'] >= 0).astype(int)

## Part 2 - Text clean up

In [ ]:
# remove punctuation

In [17]:
punc = dict.fromkeys(i for i in range(sys.maxunicode) # same code as in the book to remove punctuation
                     if unicodedata.category(chr(i)).startswith('P'))

In [18]:
txt_nopunc = [string.translate(punc) for string in df['review']] # iterates through removing the punctuation
txt_nopunc # force print

['With all this stuff going down at the moment with MJ ive started listening to his music watching the odd documentary here and there watched The Wiz and watched Moonwalker again Maybe i just want to get a certain insight into this guy who i thought was really cool in the eighties just to maybe make up my mind whether he is guilty or innocent Moonwalker is part biography part feature film which i remember going to see at the cinema when it was originally released Some of it has subtle messages about MJs feeling towards the press and also the obvious message of drugs are bad mkay<br ><br >Visually impressive but of course this is all about Michael Jackson so unless you remotely like MJ in anyway then you are going to hate this and find it boring Some may call MJ an egotist for consenting to the making of this movie BUT MJ and most of his fans would say that he made it for the fans which if true is really nice of him<br ><br >The actual feature film bit when it finally starts is only on 

In [19]:
#now make string all lower-case
text_low = [string.lower() for string in txt_nopunc] # takes block from above and applies lower
text_low

['with all this stuff going down at the moment with mj ive started listening to his music watching the odd documentary here and there watched the wiz and watched moonwalker again maybe i just want to get a certain insight into this guy who i thought was really cool in the eighties just to maybe make up my mind whether he is guilty or innocent moonwalker is part biography part feature film which i remember going to see at the cinema when it was originally released some of it has subtle messages about mjs feeling towards the press and also the obvious message of drugs are bad mkay<br ><br >visually impressive but of course this is all about michael jackson so unless you remotely like mj in anyway then you are going to hate this and find it boring some may call mj an egotist for consenting to the making of this movie but mj and most of his fans would say that he made it for the fans which if true is really nice of him<br ><br >the actual feature film bit when it finally starts is only on 

In [20]:
#remove stop words
stop_wordz = stopwords.words('english') # loads the dictionary of english stop words

In [21]:
txt_nostop = [word for word in text_low if word not in stop_wordz] #takes block from above and applies removing stop words
txt_nostop

['with all this stuff going down at the moment with mj ive started listening to his music watching the odd documentary here and there watched the wiz and watched moonwalker again maybe i just want to get a certain insight into this guy who i thought was really cool in the eighties just to maybe make up my mind whether he is guilty or innocent moonwalker is part biography part feature film which i remember going to see at the cinema when it was originally released some of it has subtle messages about mjs feeling towards the press and also the obvious message of drugs are bad mkay<br ><br >visually impressive but of course this is all about michael jackson so unless you remotely like mj in anyway then you are going to hate this and find it boring some may call mj an egotist for consenting to the making of this movie but mj and most of his fans would say that he made it for the fans which if true is really nice of him<br ><br >the actual feature film bit when it finally starts is only on 

In [ ]:
#text_low_str=text_low.apply(str)
#text_low_str = [str(x) for x in text_low]
#text_low_str = text_low.apply(lambda x: ', '.join([str(i) for i in x]))
#text_low_str = text_low.to_string()
tokens = word_tokenize(txt_nostop) # None of the above attempts allowed me to have it 'see' the text block as a 'string or byte'

In [23]:
port = PorterStemmer() # this is supposed to remove endings of words leaving the base or 'stem'
txt_stem = [port.stem(word) for word in txt_nostop] # iterate through
txt_stem # new output file

['with all this stuff going down at the moment with mj ive started listening to his music watching the odd documentary here and there watched the wiz and watched moonwalker again maybe i just want to get a certain insight into this guy who i thought was really cool in the eighties just to maybe make up my mind whether he is guilty or innocent moonwalker is part biography part feature film which i remember going to see at the cinema when it was originally released some of it has subtle messages about mjs feeling towards the press and also the obvious message of drugs are bad mkay<br ><br >visually impressive but of course this is all about michael jackson so unless you remotely like mj in anyway then you are going to hate this and find it boring some may call mj an egotist for consenting to the making of this movie but mj and most of his fans would say that he made it for the fans which if true is really nice of him<br ><br >the actual feature film bit when it finally starts is only on 

In [24]:
count = CountVectorizer()
bag_of_words = count.fit_transform(txt_stem)

In [25]:
bag_of_words.shape # yielded a higher value than the Teams chats were discussing...(!)

(25000, 112640)

In [26]:
tf = TfidfVectorizer() # I could not get this to work either. I tried importing so many different things. Never worked.

NameError: name 'TfidfVectorizer' is not defined

In [ ]:
tf_trans = tf.fit_transform(bag_of_words) # since above block failed, so did this line.

In [ ]:
# In all my classes and assignments to date, this has been by FAR the LEAST successful...